Master Notebook for Hugging Face repos Upload and Download V1

Latest version on : https://www.patreon.com/posts/104672510

In [ ]:
!pip install huggingface_hub --upgrade

!pip install ipywidgets --upgrade

Use below cell to paste your Hugging Face token key. 

If you don't see the input field, restart your session - on Massed Compute restart the CMD

Access Tokens are here : https://huggingface.co/settings/tokens

In [ ]:
# Use this cell to enter your Hugging Face token and authenticate 

from huggingface_hub import login
login()

In [ ]:
# if above fails use replace your token here and use this cell

hugging_face_token = 'your_HF_Token'

!export HUGGING_FACE_HUB_TOKEN=hugging_face_token

import subprocess

# Command to log in using the token
command = ['huggingface-cli', 'login', '--token', hugging_face_token]

# Execute the command
subprocess.run(command, check=True)

In [ ]:
# This cell is used to upload single file into a repo with certain name

from huggingface_hub import HfApi
api = HfApi()
api.upload_file(
    path_or_fileobj=r"/home/Ubuntu/apps/stable-diffusion-webui/models/Stable-diffusion/model_name.safetensors",
    path_in_repo="model_name.safetensors",
    repo_id="YourUserName/reponame",
    repo_type="model",
)

In [ ]:
# This cell is used to upload a folder into a repo with single commit

from huggingface_hub import HfApi
api = HfApi()
api.upload_folder(
    folder_path=r"/home/Ubuntu/apps/stable-diffusion-webui/models/Stable-diffusion",
    repo_id="YourUserName/reponame",
    repo_type="model",
)

To upload all files in given folder to the target Hugging Face repository use below

In [ ]:
# This cell uploads a folder into remote repo with multi commit
# Supports continue feature so if gets interrupted you can run again to continue / resume

from huggingface_hub import HfApi
from huggingface_hub import get_collection, delete_collection_item
from huggingface_hub import upload_file
from huggingface_hub import (
    HfFolder,
    ModelCard,
    ModelCardData,
    create_repo,
    hf_hub_download,
    upload_folder,
    whoami,
)
api = HfApi()
upload_folder(
    folder_path=r"/home/Ubuntu/apps/stable-diffusion-webui/models/Stable-diffusion",
    repo_id="YourUserName/reponame",
    repo_type="model",
    multi_commits=True,
    multi_commits_verbose=True,
)


To download all files in given Hugging Face repository use below

In [ ]:
# This cell downloads all files from given repo 1 by 1 
# This is not same as clone and it is faster and more convenient to use 

!pip install tqdm --upgrade

import os
import requests
from huggingface_hub import list_repo_files, hf_hub_url
from huggingface_hub.utils import HfFolder
from tqdm import tqdm

# Define the repository and target folder
repo_id = "YourUserName/reponame"
target_folder = "/home/Ubuntu/apps/stable-diffusion-webui/models/Stable-diffusion"

# Retrieve the token from the .huggingface folder or set it manually
token = HfFolder.get_token()
# or set your token directly
# token = "your_huggingface_token"

if not token:
    raise ValueError("Hugging Face token not found. Please log in using `huggingface-cli login` or set the token manually.")

headers = {
    "Authorization": f"Bearer {token}"
}

# List all files in the repository
files = list_repo_files(repo_id)

# Ensure the target folder exists
os.makedirs(target_folder, exist_ok=True)

# Download each file directly to the target folder
for file in files:
    try:
        # Define the target path for the file
        target_path = os.path.join(target_folder, file)
        
        # Check if the file already exists
        if os.path.exists(target_path):
            print(f"File {file} already exists. Skipping download.")
            continue
        
        # Get the URL for the file
        file_url = hf_hub_url(repo_id, filename=file, repo_type='model')
        
        # Ensure subdirectories exist
        os.makedirs(os.path.dirname(target_path), exist_ok=True)
        
        # Download the file with authentication
        response = requests.get(file_url, headers=headers, stream=True)
        response.raise_for_status()  # Raise an error for bad status codes
        
        # Get the total file size from the response headers
        total_size = int(response.headers.get('content-length', 0))
        
        # Progress bar setup
        with tqdm(total=total_size, unit='B', unit_scale=True, desc=file, initial=0, ascii=True) as pbar:
            # Write the file to the target path
            with open(target_path, 'wb') as f:
                for chunk in response.iter_content(chunk_size=8192):
                    if chunk:
                        f.write(chunk)
                        pbar.update(len(chunk))
        
        # Set the correct permissions for the downloaded file
        os.chmod(target_path, 0o644)  # Read and write for owner, read for group and others
    
    except Exception as e:
        print(f"An error occurred while processing file {file}: {e}")

print(f"All files have been downloaded to {target_folder}")